In [1]:
import pandas as pd
import math
import pickle as pkl

from torch_geometric.data import Data
import torch
import tqdm

In [11]:
## Preprocessing
df = pd.read_csv("reddit.csv")
print(df.shape)

# select columns
df_graph = df[
    [
        "subreddit_id",
        "subreddit",
        "name",
        "body",
        "score",
        "author",
        "author_flair_text",
        "distinguished",
    ]
]
df_graph.rename(
    columns={
        "name": "post_id",
        "body": "post",
        "author": "user",
        "author_flair_text": "user_flair",
    },
    inplace=True,
    errors="raise",
)

# drop na, duplicates and deleted post
df_graph = df_graph.drop_duplicates()
df_graph = df_graph[df_graph["post"] != "[deleted]"]
df_graph = df_graph.dropna(subset=["post_id"])
df_graph = df_graph.dropna(subset=["user_flair"])
df_graph = df_graph.dropna(subset=["subreddit"])
df_graph = df_graph.dropna(subset=["post"])
print(df_graph.shape)

df_graph["distinguished"] = df_graph["distinguished"].apply(
    lambda x: "ordinary" if pd.isna(x) else "distinguished"
)
df_graph["user_flair"] = df_graph["user_flair"].apply(lambda x: "" if pd.isna(x) else x)

/tmp/ipykernel_5327/3476166533.py:2: DtypeWarning: Columns (2,3,4,6,7,8,9,14,17,18,21) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("reddit.csv")


(1070077, 22)


/tmp/ipykernel_5327/3476166533.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_graph.rename(


(256388, 8)


In [12]:
df = df_graph
df.head(1)

subreddit_id   subreddit     post_id  \
3     t5_2qhon  comicbooks  t1_cqug9dk   

                                                post  score         user  \
3  It's not contradictory. Snyder's rendition of ...    1.0  eskimo_bros   

  user_flair distinguished  
3  Luke Cage      ordinary

In [14]:
text_nodes = []
node_labels = []
sub_id2idx = {}
sub_nodes = []
user_id2idx = {} 
user_nodes = []
count = 0
text_edges = []
for _, row in tqdm.tqdm(df.iterrows()):
    sub_id = str(row["subreddit"])
    user_id = str(row['user'])

    if sub_id not in sub_id2idx:
        sub_id2idx[sub_id] = count
        sub_nodes.append(count)
        count += 1
    else:
        sub_nodes.append(sub_id2idx[sub_id])
    text_nodes.append(f"subreddit {sub_id}")
    node_labels.append(-1)

    if user_id not in user_id2idx:
        user_id2idx[user_id] = count
        user_nodes.append(count)
        count += 1
    else:
        user_nodes.append(user_id2idx[user_id])
    text_nodes.append(f"user {user_id} has flair {row['user_flair']}")
    node_labels.append(row['distinguished'])
    text_edges.append(str(row['post']))
    

## Save it as torch data
graph = Data(
    text_nodes=text_nodes,
    text_edges=text_edges,
    node_labels=node_labels,
    edge_index=torch.tensor([user_nodes, sub_nodes], dtype=torch.long),
)

with open("../processed/reddit.pkl", "wb") as file:
    pkl.dump(graph, file)

256388it [00:15, 17023.98it/s]
